In [2]:
import plotly.graph_objects as go 
import matplotlib.pyplot as plt
import numpy as np
import scipy.constants as cst
from pint import UnitRegistry

In [3]:
unit = UnitRegistry()
a = 1 * unit.nanometer
b = 15 * unit.second

(a/b).to('meter/minute')

<Quantity(4e-09, 'meter / minute')>

<span style="font-size:40px;">**Niveau 1**</span>


In [4]:
class Maillage : 
    #Initialisation de l'objet.
    def __init__(self,X : np.ndarray ,Y : np.ndarray,Z : np.ndarray) :         
        if not((size := X.size) == Y.size == Z.size) : 
            raise ValueError('Les 3 matrices doivent avoir les mêmes dimensions.')
        
        #Les listes sont flatten par convénience.
        X,Y,Z = X.flatten(),Y.flatten(),Z.flatten()
        self.X = X
        self.Y = Y
        self.Z = Z
        self.XYZ = np.array([X,Y,Z])
        self.nb_points = size
    
    #Définition de l'addition de "Maillage1 + Maillage2".
    def __add__(self,maillage : "Maillage") -> "Maillage" : 
        X,Y,Z = np.concatenate((self.X,maillage.X)),np.concatenate((self.Y,maillage.Y)),np.concatenate((self.Z,maillage.Z))
        return  Maillage(X,Y,Z) 
    
    #Définition de la multiplication scalaire ie "scalaire * Maillage".
    def __rmul__(self,scalaire) :
        return Maillage(scalaire*self.X,scalaire*self.Y,scalaire*self.Z) 
    
    #Définition de l'expression Maillage[indice].
    def __getitem__(self,index : int) -> "Maillage" : 
        return self.X[index],self.Y[index],self.Z[index]
    
    #Définition de l'égalité entre deux maillages ie "Maillage1 == Maillage2".
    def __eq__(self, maillage : "Maillage"):
        return np.array_equal(self.X, maillage.X) and \
               np.array_equal(self.Y, maillage.Y) and \
               np.array_equal(self.Z, maillage.Z)


    def translate(self, dl : tuple[float]) -> "Maillage":
        if len(dl) != 3:
            raise ValueError('Trop ou pas assez de translations ont été données.')

        return Maillage(self.X + dl[0], self.Y + dl[1], self.Z + dl[2])
    
    def norm(self) : 
        return np.sqrt(self.X**2 + self.Y**2 + self.Z**2)
    
    def rotate(self, axes : list[str], angles : list[float]) -> "Maillage" : 
        if len(axes) != len(angles):
            raise ValueError("Trop ou pas assez d'angles et/ou axes ont été donnés.")

        Rx = lambda angle : np.array([[1,0,0],[0,np.cos(angle),-np.sin(angle)],[0,np.sin(angle),np.cos(angle)]])
        Ry = lambda angle : np.array([[np.cos(angle),0,np.sin(angle)],[0,1,0],[-np.sin(angle),0,np.cos(angle)]])
        Rz = lambda angle : np.array([[np.cos(angle),-np.sin(angle),0],[np.sin(angle),np.cos(angle),0],[0,0,1]])
        product = ''
    
        for axe,angle in zip(axes,angles) : 
            product = f'R{axe.strip().lower()}({angle}) @' + product
        
        return Maillage(*eval(f'{product} self.XYZ')) 
    


In [5]:
def cylindrique_to_cartesien(r : float, theta : float, z : float) -> tuple:
    """
    Entrées :
        - r: valeur du rayon (distance entre le point et son projeté orthogonal sur l'axe du cylindre).
        - theta: valeur de l’angle.
        - z: valeur de l'altitude.

    Sortie :
        - Renvoie un couple (x,y,z) représentant les coordonnées du point en cartésien.

    Explication:
        - Prend des coordonnées cylindriques et les traduit en coordonnées cartésiennes.
    """
    return r*np.cos(theta), r*np.sin(theta), z

In [6]:
def spherique_to_cartesien(r : float, theta : float, phi : float) -> tuple:
    """
    Entrées :
        - r : valeur du rayon.
        - theta : valeur de l’angle entre OM (M point quelconque de l’espace) et Oz.
        - phi : valeur de l’angle entre le projeté orthogonal de OM sur le plan (xOy) et l’axe Ox.
    
    Sortie :
        - Renvoie un couple (x,y,z) représentant les coordonnées du point en cartésien.

    Explication:
        - Prend des coordonnées sphériques et les traduit en coordonnées cartésiennes.
    """
    return r * np.cos(phi) * np.sin(theta), r * np.sin(phi) * np.sin(theta), r * np.cos(theta)

<span style="font-size:40px;">**Niveau 2**</span>


In [7]:
def creer_maillage_plan(x_min : float, x_max : float, y_min : float, y_max : float, z : "function", pas_x : float, pas_y : float) -> Maillage : 
    densite_x = int(1/pas_x)
    densite_y = int(1/pas_y)
    
    x = np.linspace(x_min,x_max, densite_x*int(x_max - x_min)+1)
    y = np.linspace(y_min,y_max, densite_y*int(y_max - y_min)+1)
    X,Y = np.meshgrid(x,y)
    Z = np.full_like(X, z(X, Y))
    
    return Maillage(X,Y,Z)

In [8]:
def creer_maillage_cartesien(x_min : float, x_max : float, y_min : float, y_max : float, z_min : float, z_max : float, pas_du_maillage : float) -> Maillage : 
    M = Maillage(*np.empty((3,0)))
    densite_x = int(1/pas_du_maillage)
    Z = np.linspace(z_min,z_max, densite_x*int(z_max - z_min)+1)
    
    for z in Z : 
        M += creer_maillage_plan(x_min,x_max,y_min,y_max,lambda x,y : z, pas_du_maillage,pas_du_maillage)
    
    return M

In [9]:
def creer_maillage_cylindrique(z_min : float, z_max : float, rayon : "function", theta : float, pas_z : float, pas_theta : float) -> Maillage :
    """
    Entrées :

        - z_min : Représente la valeur minimale selon z.
        - z_max : Représente la valeur maximale selon z.
            - NB : Z_max – Z_min = hauteur.

        - rayon : C’est une fonction, elle dépend de theta et de z.
        - theta : représente l’angle d’ouverture ducylindre.

        - pas_du_maillage :

            * Distance séparant 2 points (non diagonnaux) du maillage.

            * Il est de préférence un diviseur de (theta_max - theta_min) et de(rayon_max - rayon_min) et (z_max - z_min).

            * Éviter un pas égal à 0.3 ou quelconque multiple de 0.3 ainsi que les nombres premiers par exemple.

            * Sa valeur ne doit pas être plus élevée que la moitié de la plus petite distance coordonnée_max - coordonnée_min des 3 axes.

    - Sorties :
    
        - Renvoie un maillage qui représente un cylindre ou un morceau de cylindre en fonction de l’angle annoncé.
    """

    #je ne sais pas si ces conditions sont utiles

    if theta > 2 * np.pi:
        theta = 2 * np.pi

    densite_theta = int(1/pas_theta)
    densite_z = int(1/pas_z)

    valeurs_theta = np.linspace(0, theta, densite_theta * int(theta),endpoint=False) 
    valeurs_z = np.linspace(z_min, z_max, densite_z*int(z_max - z_min) + 1,endpoint=False)

    THETA, Z = np.meshgrid(valeurs_theta, valeurs_z)
    array_r = np.full_like(THETA,rayon(THETA,Z))

    return Maillage(*cylindrique_to_cartesien(array_r, THETA, Z))

In [10]:
def creer_maillage_spherique(rayon : "function", theta : float, phi : float, pas_phi : float, pas_theta : float) -> Maillage :
    densite_phi = int(1/pas_phi)
    densite_theta = int(1/pas_theta)
    
    Theta = np.linspace(0, theta, densite_theta * int(theta),endpoint=False) 
    Phi =  np.linspace(0, phi, densite_phi * int(phi),endpoint=False) 

    THETA, PHI = np.meshgrid(Theta,Phi)
    RAYON = np.full_like(THETA,rayon(THETA,PHI))
    
    return Maillage(*spherique_to_cartesien(RAYON,THETA,PHI))

In [11]:
def creer_cercle(rayon : float, theta : float, z : 'function', pas : float):
    Theta = np.linspace(0,theta, int((1/pas)*theta*rayon))
    Rayon = np.full_like(Theta, rayon, float)
    RAYON, THETA = np.meshgrid(Rayon, Theta)
    Z = np.full_like(RAYON,z(THETA,RAYON))
    
    return Maillage(*cylindrique_to_cartesien(RAYON,THETA,Z))

In [12]:
def creer_maillage_disque(rayon : float, theta : float, z : "function", pas_rayon : float, pas_theta : float) -> Maillage : 
    densite_rayon = int(1/pas_rayon)
    disque = Maillage(*np.empty((3,0)))
    
    for r in np.linspace(0, rayon, densite_rayon * int(rayon)):
        disque += creer_cercle(r,theta,z,pas_theta)
    return disque

test = creer_maillage_disque(2,2*np.pi,lambda theta,rayon : 2,0.1,0.1)

<span style="font-size:40px;">**Niveau 3**</span>


In [13]:
def calcule_charge(maillage: Maillage, distribution_charge : tuple[float,"function"] = None) : 
    return (val := distribution_charge[1](*maillage.XYZ))*distribution_charge[0]/np.sum(val) if distribution_charge != None else None
    
def afficher_plotly(maillage : Maillage, distribution_charge : tuple[float,"function"] = None) : 
    fig = go.Figure(go.Scatter3d(x=maillage.X,y=maillage.Y,z=maillage.Z,mode="markers",
                                 marker=dict(color=calcule_charge(maillage,distribution_charge),colorscale="Viridis",showscale=True if distribution_charge != None else False,size=1)))
    fig.show()

def afficher_matplotlib(maillage : Maillage, distribution_charge : tuple[float,"function"] = None) :

    fig = plt.figure(figsize=(8, 6))
    ax = fig.add_subplot(111, projection='3d')
    sc = ax.scatter(maillage.X, maillage.Y, maillage.Z, marker='o', c = calcule_charge(maillage,distribution_charge), cmap="coolwarm", s = 0.5)

    if distribution_charge is not None:
        cbar = fig.colorbar(sc, ax=ax, shrink=0.5)
        cbar.set_label("valeurs")
    ax.set_xlabel("X")
    ax.set_ylabel("Y")

    plt.show()

In [14]:
def isoler_plan_cartesien(M : Maillage, plan : str, valeur_coupe : float) -> Maillage :
    plan = ''.join(sorted(plan.strip().lower()))
    index = {'yz' : 0,'xz' : 1,'xy' : 2}
    mask = M.XYZ[index[plan],:] == valeur_coupe
    if np.any(mask) == False : raise ValueError("la valeur de coupe choisit n'est pas autorisée")
    return Maillage(* M.XYZ[:,mask]) 

In [15]:
x_min,x_max,y_min,y_max,z_min,z_max = -2,2,-3,4,0,5
pas_du_maillage = 0.5
Maillage_espace = creer_maillage_cartesien(x_min,x_max,y_min,y_max,z_min,z_max,pas_du_maillage)
#afficher_plotly(isoler_plan_cartesien(Maillage_espace, 'yz',0))

In [16]:
sphere = creer_maillage_spherique(lambda theta,phi : 2,np.pi,2*np.pi,0.01,0.01)
afficher_plotly(sphere,(10,lambda x,y,z : abs(x)))

In [17]:
k= 1/(4*np.pi*cst.epsilon_0)
charge = Maillage(*np.array([[3,2],[2,7],[1,0]])) # OP 
print(charge.XYZ)
point = np.array([-2,0,1]) # OM 
q = 1.6*10**(-8)
u = -1*charge.translate(-point) # PM = PO + OM = OM - OP
norme = u.norm()
vect = k*q*u.XYZ/norme**3

fig = go.Figure()

fig.add_traces(go.Scatter3d(
    x = [point[0],point[0] + vect[0,0]],
    y = [point[1],point[1] + vect[1,0]],
    z = [point[2],point[2] + vect[2,0]]
)) #vecteur 1

fig.add_traces(go.Scatter3d(
    x = [point[0],point[0] + vect[0,1]],
    y = [point[1],point[1] + vect[1,1]],
    z = [point[2],point[2] + vect[2,1]]
)) # vecteur 2

vect_totale = np.sum(vect,axis=1)
fig.add_traces(go.Scatter3d(
    x = [point[0],point[0] + vect_totale[0]],
    y = [point[1],point[1] + vect_totale[1]],
    z = [point[2],point[2] + vect_totale[2]]
)) # vecteur 2

fig.add_traces(go.Scatter3d(
    x = charge.X,
    y = charge.Y,
    z = charge.Z,
    mode="lines+markers"
))

[[3 2]
 [2 7]
 [1 0]]


In [18]:
def creer_maillage_disque(rayon : float, theta : float, z : "function", pas_rayon : float, pas_theta : float) -> Maillage : 
    densite_rayon = int(1/pas_rayon)
    densite_theta = int(1/pas_theta)
    
    Theta = np.linspace(0, theta, densite_theta * int(theta),endpoint=False) 
    Rayon =  np.linspace(0, rayon, densite_rayon * int(rayon)) 

    THETA, RAYON = np.meshgrid(Theta,Rayon)
    Z = np.full_like(THETA,z(THETA,RAYON))
    
    return Maillage(*cylindrique_to_cartesien(RAYON, THETA, Z))

In [19]:
k= 1/(4*np.pi*cst.epsilon_0)
#plan = creer_maillage_plan(-2,2,-2,2, lambda x,y : 0,0.1,0.1)
plan = creer_maillage_disque(2,2*np.pi, lambda theta,r : 0,0.1,0.1)
point = np.array([0,0,1])

q = 1.6*10**(-12)
u = -1*plan.translate(-point)
norme = u.norm()
vect = np.sum(k*q*u.XYZ/norme**3,axis=1)

fig = go.Figure()

fig.add_traces(go.Scatter3d(
    x = plan.X,
    y = plan.Y,
    z = plan.Z,
    mode="markers",
    marker=dict(size=1))
)

fig.add_traces(go.Scatter3d(
    x = [point[0],point[0] + vect[0]],
    y = [point[1],point[1] + vect[1]],
    z = [point[2],point[2] + vect[2]],
    mode="lines+markers",
    marker=dict(size=3))
)